In [151]:
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import numpy as np
import pandas as pd
from scipy.spatial import cKDTree
from math import sqrt, ceil
from scipy.stats import linregress
from sympy.physics.mechanics import potential_energy

import libraries as lib
import math 

In [152]:
directory = "/Users/willemheemskerk/Downloads/20230525_h2a_poging1/0002/"
    #"../../HvA/CleanMobility - E-team/Logfiles/H2A/2023/Nogaro/20230525_h2a_poging1/0002/"
file_master = "1.csv"
file_motordriver ="5.csv"
file_FCC = "4.csv"
file_richting = "F.csv"

In [153]:
data_file_motordriver = lib.DataInladenMotorDriver(f'{directory}{file_motordriver}')
data_file_master = lib.DataInladen(f'{directory}{file_master}')
data_file_FCC = lib.DataInladenFCC(f'{directory}{file_FCC}')
data_file_richting = lib.DataInladen(f'{directory}{file_richting}')

In [154]:
data_file_motordriver["GPS longitude, in graden"] = data_file_motordriver["GPS longitude, in graden"]* -1
data_file_motordriver

Datalogger port  Dataloggertijd, in s Format header (>03|04)  \
0                     5              252.6246                  03|04   
1                     5              252.6305                  03|04   
2                     5              252.6362                  03|04   
3                     5              252.6420                  03|04   
4                     5              252.6478                  03|04   
...                 ...                   ...                    ...   
496050                5             6919.3279                  03|04   
496051                5             6919.3363                  03|04   
496052                5             6919.3448                  03|04   
496053                5             6919.3533                  03|04   
496054                5             6919.3618                  03|04   

        Tijd sinds laatste herstart motordriver (s)  \
0                                            0.0060   
1                                            0.0118   
2                                            0.0176   
3                                            0.0234   
4                                            0.0292   
...                                             ...   
496050                                    3277.5222   
496051                                    3277.5308   
496052                                    3277.5393   
496053                                    3277.5479   
496054                                    3277.5562   

        Spanning over de motor (V)  Stroom door de motor (A)  \
0                            2.725                    -0.003   
1                            4.996                    -0.006   
2                            7.028                    -0.008   
3                            8.845                    -0.010   
4                           10.471                    -0.010   
...                            ...                       ...   
496050                       0.039                     0.114   
496051                       0.039                     0.122   
496052                       0.040                     0.129   
496053                       0.040                     0.141   
496054                       0.041                     0.154   

        Vermogen geleverd aan de motor (W)  \
0                                     -0.1   
1                                     -0.1   
2                                     -0.2   
3                                     -0.2   
4                                     -0.2   
...                                    ...   
496050                                 0.0   
496051                                 0.0   
496052                                 0.0   
496053                                 0.0   
496054                                 0.0   

        Energie geleverd aan de motor sinds reset (J)  \
0                                                   0   
1                                                   0   
2                                                   0   
3                                                   0   
4                                                   0   
...                                               ...   
496050                                         181490   
496051                                         181490   
496052                                         181490   
496053                                         181490   
496054                                         181490   

        Spanning aan de ingang van motordriver (V)  \
0                                            3.034   
1                                            5.562   
2                                            7.823   
3                                            9.846   
4                                           11.655   
...                                            ...   
496050                                       9.762   
496051                                     

In [90]:
import pandas as pd
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

def convert_to_decimal(degrees_minutes, direction):
    degrees = int(degrees_minutes[:2])
    minutes = float(degrees_minutes[2:])
    decimal = degrees + minutes / 60
    if direction in ['S', 'W']:
        decimal = -decimal
    return decimal

def lees_gps_data(filepath):
    latitudes = []
    longitudes = []
    hoogtes = []
    
    with open(filepath, 'r') as file:
        for regel in file:
            if regel.startswith('$GPGGA'):
                delen = regel.split(',')
                if len(delen) > 9:
                    latitude = delen[2]
                    lat_direction = delen[3]
                    longitude = delen[4]
                    lon_direction = delen[5]
                    hoogte = delen[9]
                    
                    # Converteren van NMEA formaat naar decimale graden
                    if latitude and longitude:
                        dec_lat = convert_to_decimal(latitude, lat_direction)
                        dec_lon = convert_to_decimal(longitude, lon_direction)
                        latitudes.append(dec_lat)
                        longitudes.append(dec_lon)
                        
                    # Hoogte extraheren
                    try:
                        hoogte = float(hoogte)
                        hoogtes.append(hoogte)
                    except ValueError:
                        continue

    # Maak een DataFrame van de verzamelde gegevens
    data = pd.DataFrame({
        'latitude': latitudes,
        'longitude': longitudes,
        'hoogte': hoogtes
    })
    return data

# Bestandspad instellen
file_path = '/Users/willemheemskerk/Downloads/20230525_h2a_poging1/0002/data voor hoogteprofiel.txt'

# Lees de GPS-data
df = lees_gps_data(file_path)
df


latitude  longitude  hoogte
0      43.771393  -0.042098    99.5
1      43.771393  -0.042098    99.5
2      43.771393  -0.042098    99.4
3      43.771392  -0.042098    99.5
4      43.771393  -0.042098    99.4
...          ...        ...     ...
46568  43.771202  -0.041941    96.0
46569  43.771202  -0.041941    96.0
46570  43.771202  -0.041941    96.1
46571  43.771202  -0.041941    96.1
46572  43.771202  -0.041941    96.2

[46573 rows x 3 columns]

In [155]:
def lees_gps_data(filepath):
    """Read GPS data from a text file and convert to a DataFrame."""
    timestamps = []
    latitudes = []
    longitudes = []
    hoogtes = []
    speeds = []
    
    with open(filepath, 'r') as file:
        for regel in file:
            parts = regel.split(',')
            if regel.startswith('$GPRMC'):
                # Extract time and speed from GPRMC sentence
                if len(parts) > 7:
                    timestamp = parts[1]
                    speed = parts[7]  # Speed in knots
                    timestamps.append(timestamp)
                    try:
                        speed_kmh = (float(speed) * 1.852) /3.6 # Convert knots to km/h
                        speeds.append(speed_kmh)
                    except ValueError:
                        speeds.append(None)

            elif regel.startswith('$GPGGA'):
                # Extract latitude, longitude, and altitude from GPGGA sentence
                if len(parts) > 9:
                    latitude = parts[2]
                    lat_direction = parts[3]
                    longitude = parts[4] 
                    lon_direction = parts[5]
                    altitude = parts[9]
                    
                    # Convert latitude and longitude
                    try:
                        latitude = float(latitude)
                        latitudes.append(latitude)
                    except ValueError:
                        latitudes.append(None)
                    
                    if lon_direction in ['W']:
                        longitude = float(longitude)
                        longitude = -longitude 
                        longitudes.append(longitude)
                    else:
                        longitudes.append(None)
                    # Convert altitude to float
                    try:
                        altitude = float(altitude)
                        hoogtes.append(altitude)
                    except ValueError:
                        hoogtes.append(None)
    
    # Check if all lists have the same length
    max_length = max(len(timestamps), len(latitudes), len(longitudes), len(hoogtes), len(speeds))
    
    # Make sure all lists have the same length by appending None to the shorter ones
    timestamps.extend([None] * (max_length - len(timestamps)))
    latitudes.extend([None] * (max_length - len(latitudes)))
    longitudes.extend([None] * (max_length - len(longitudes)))
    hoogtes.extend([None] * (max_length - len(hoogtes)))
    speeds.extend([None] * (max_length - len(speeds)))
    
    # Construct DataFrame
    data = {
        'timestamp': timestamps,
        'latitude': latitudes,
        'longitude': longitudes,
        'hoogte': hoogtes,
        'speed_m/s': speeds
    }
    
    df = pd.DataFrame(data)
    
    # Filter out rows where latitude or longitude are missing
    df = df.dropna(subset=['latitude', 'longitude']).reset_index(drop=True)
    return df

# Set file path
file_path = '/Users/willemheemskerk/Downloads/20230525_h2a_poging1/0002/data voor hoogteprofiel.txt'

# Read GPS data
df = lees_gps_data(file_path)

# Print the resulting DataFrame
df


timestamp    latitude  longitude  hoogte  speed_m/s
0      063448.30  4346.28356   -2.52589    99.5   0.038583
1      063448.40  4346.28356   -2.52589    99.5   0.026237
2      063448.50  4346.28356   -2.52589    99.4   0.035497
3      063448.60  4346.28355   -2.52589    99.5   0.073051
4      063448.70  4346.28356   -2.52589    99.4   0.064820
...          ...         ...        ...     ...        ...
46568       None  4346.27213   -2.51648    96.0        NaN
46569       None  4346.27213   -2.51648    96.0        NaN
46570       None  4346.27213   -2.51648    96.1        NaN
46571       None  4346.27212   -2.51647    96.1        NaN
46572       None  4346.27213   -2.51649    96.2        NaN

[46573 rows x 5 columns]

In [122]:
def filter_track_data(df, start_lon, start_lat, end_lon, end_lat):
    start_index = find_nearest_index(df, start_lon, start_lat)
    end_index = find_nearest_index(df, end_lon, end_lat)
    
    # Zorg ervoor dat de start_index voor de end_index komt
    if start_index > end_index:
        start_index, end_index = end_index, start_index
    
    return df.iloc[start_index:end_index + 1]


In [123]:
# Definieer de coördinaten voor het start- en eindpunt
start_lon = -0.0445
start_lat = 0.0019 + 4.377e1
end_lon = -0.040
end_lat = 0.00025 + 4.377e1

# Veronderstel dat 'df' je DataFrame is met de relevante data
filtered_df = filter_track_data(df, start_lon, start_lat, end_lon, end_lat)

# Print het gefilterde DataFrame om te controleren
print(filtered_df)


       timestamp    latitude  longitude  hoogte  speed_kmh
43093  074735.40  4346.21583   -2.40475    97.9  23.642632


In [145]:

def plot_hoogteprofiel(latitudes, longitudes, hoogtes):
    fig = plt.figure()
    ax = fig.add_subplot(111, projection='3d')
    scatter = ax.scatter(longitudes, latitudes, hoogtes, c=hoogtes, cmap='viridis')
    ax.set_title('3D Hoogteprofiel')
    ax.set_xlabel('Longitude')
    ax.set_ylabel('Latitude')
    ax.set_zlabel('Hoogte (m)')
    plt.show()

plot_hoogteprofiel(df['latitude'], df['longitude'],df['hoogte'])


In [35]:
def filter_data(data, min_lon, max_lon, min_lat, max_lat, min_hoogte, max_hoogte):
    """ Filter de punten die zich binnen de gedefinieerde pitstraat coördinaten en irreële hoogtes bevinden. """
    gefilterde_data = data[
        ((data['longitude'] < min_lon) | (data['longitude'] > max_lon) |
         (data['latitude'] < min_lat) | (data['latitude'] > max_lat)) &
        (data['hoogte'] >= min_hoogte) & (data['hoogte'] <= max_hoogte)
    ]
    return gefilterde_data

# Filtergrenzen instellen
min_lon = -0.044
max_lon = -0.040
min_lat = 0.00025+4.377e1
max_lat = 0.0019+4.377e1
min_hoogte = 96
max_hoogte = 105

# Pas de filter toe
gefilterde_data = filter_data(df, min_lon, max_lon, min_lat, max_lat, min_hoogte, max_hoogte)


In [118]:
import pandas as pd
import numpy as np

def calculate_distance(lat1, lon1, lat2, lon2):
    return np.sqrt((lat2 - lat1) ** 2 + (lon2 - lon1) ** 2)

def find_nearest_index(df, target_lon, target_lat):
    distances = df.apply(lambda row: calculate_distance(row['latitude'], row['longitude'], target_lat, target_lon), axis=1)
    return distances.idxmin()


In [193]:
%matplotlib qt

import matplotlib.pyplot as plt

def plot_hoogteprofiel_2d(latitudes, longitudes, hoogtes):
    # Increase figure size by setting the figsize
    fig, ax = plt.subplots(figsize=(12, 8))  # Adjust the width and height as needed
    scatter = ax.scatter(longitudes, latitudes, c=hoogtes, cmap='viridis', marker='o')
    ax.set_title('Hoogteprofiel van racebaan Nogaro', fontsize=16)
    ax.set_xlabel('Longitude', fontsize=14)
    ax.set_ylabel('Latitude', fontsize=14)
    
    # Create the colorbar
    cbar = fig.colorbar(scatter, ax=ax)
    cbar.set_label('Hoogte boven zeeniveau (m)', fontsize=12)
    
    # Define boundaries
    lat_min, lat_max = 0.0078 + 4.34635e3, 0.00805 + 4.34635e3
    lon_min, lon_max = -2.553, -2.546
    
    lat_min2, lat_max2 = 0.0005 + 4.346245e3, 0.0009 + 4.346245e3
    lon_min2, lon_max2 = -2.392, -2.386

    # Plot the rectangular boundaries
    plt.plot(
        [lon_min, lon_max, lon_max, lon_min, lon_min],
        [lat_min, lat_min, lat_max, lat_max, lat_min],
        color='red', linestyle='--', linewidth=2, label="Boundary Square")

    plt.plot(
        [lon_min2, lon_max2, lon_max2, lon_min2, lon_min2],
        [lat_min2, lat_min2, lat_max2, lat_max2, lat_min2],
        color='red', linestyle='--', linewidth=2, label="Boundary Square")

    for i in range(len(latitudes)):
        lat = latitudes.iloc[i]
        lon = longitudes.iloc[i]
        plt.text(lon, lat, str(i), fontsize=8, color='black')

    # Enable grid
    plt.grid(True)
    
    # Show the plot
    plt.show()

# Assuming `df` is your DataFrame with columns: 'latitude', 'longitude', and 'hoogte'
plot_hoogteprofiel_2d(df['latitude'], df['longitude'], df['hoogte'])


In [29]:
import plotly.graph_objects as go

def plot_interactive_3d(latitudes, longitudes, hoogtes):
    fig = go.Figure(data=[go.Scatter3d(
        x=longitudes,
        y=latitudes,
        z=hoogtes,
        mode='markers',
        marker=dict(
            size=5,
            color=hoogtes,  # kleur punten door hoogte
            colorscale='Viridis',  # kleurenschaal
            opacity=0.8
        )
    )])

    fig.update_layout(
        title='Interactief 3D Hoogteprofiel',
        scene=dict(
            xaxis_title='Longitude',
            yaxis_title='Latitude',
            zaxis_title='Hoogte (m)'
        ),
        margin=dict(l=0, r=0, b=0, t=0)  # Verminder de witruimte rond de plot
    )
    
    # Bewaar de plot als HTML bestand
    plot_path = 'C:/Users/qvled/OneDrive - HvA/Clean_Mobility_Files/H2A/interactive_3d_plot.html'
    fig.write_html(plot_path)
    print(f"Plot opgeslagen als {plot_path}")

    fig.show()

# Gebruik de functie met de gefilterde data
plot_interactive_3d(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


Plot opgeslagen als C:/Users/qvled/OneDrive - HvA/Clean_Mobility_Files/H2A/interactive_3d_plot.html


In [30]:
import plotly.graph_objects as go

def plot_interactive_3d(latitudes, longitudes, hoogtes):
    fig = go.Figure(data=[go.Scatter3d(
        x=longitudes,
        y=latitudes,
        z=hoogtes,
        mode='markers',
        marker=dict(
            size=5,
            color=hoogtes,  # kleur punten door hoogte
            colorscale='Viridis',  # kleurenschaal
            opacity=0.8
        )
    )])

    # Aanpassen van de aspectratio om een realistischere 3D weergave te krijgen
    fig.update_layout(
        scene=dict(
            aspectmode='manual',
            aspectratio=dict(x=1, y=1, z=0.1),  # Aanpassen van de z-as schaal
            xaxis_title='Longitude',
            yaxis_title='Latitude',
            zaxis_title='Hoogte (m)'
        ),
        title='Interactief 3D Hoogteprofiel',
        margin=dict(l=0, r=0, b=0, t=0)  # Verminder de witruimte rond de plot
    )
    
    # Bewaar de plot als HTML bestand
    plot_path = 'C:/Users/qvled/OneDrive - HvA/Clean_Mobility_Files/H2A/interactive_3d_plot.html'
    fig.write_html(plot_path)
    print(f"Plot opgeslagen als {plot_path}")

    fig.show()

# Gebruik de functie met de gefilterde data
plot_interactive_3d(filtered_df['latitude'], filtered_df['longitude'], filtered_df['hoogte'])


Plot opgeslagen als C:/Users/qvled/OneDrive - HvA/Clean_Mobility_Files/H2A/interactive_3d_plot.html


In [157]:
df

timestamp    latitude  longitude  hoogte  speed_m/s
0      063448.30  4346.28356   -2.52589    99.5   0.038583
1      063448.40  4346.28356   -2.52589    99.5   0.026237
2      063448.50  4346.28356   -2.52589    99.4   0.035497
3      063448.60  4346.28355   -2.52589    99.5   0.073051
4      063448.70  4346.28356   -2.52589    99.4   0.064820
...          ...         ...        ...     ...        ...
46568       None  4346.27213   -2.51648    96.0        NaN
46569       None  4346.27213   -2.51648    96.0        NaN
46570       None  4346.27213   -2.51648    96.1        NaN
46571       None  4346.27212   -2.51647    96.1        NaN
46572       None  4346.27213   -2.51649    96.2        NaN

[46573 rows x 5 columns]

In [203]:
import numpy as np

# Set initial flag and empty list
gevonden = False
rechtestuk_rijen = []

# Define the coordinates for the two rectangular areas
lat_min, lat_max = 0.0078 + 4.34635e3, 0.00805 + 4.34635e3
lon_min, lon_max = -2.553, -2.546

lat_min2, lat_max2 = 0.0005 + 4.346245e3, 0.0009 + 4.346245e3
lon_min2, lon_max2 = -2.392, -2.386

# Iterate over each row in the DataFrame (replace df with your actual DataFrame)
for i in range(len(df)):
    lat = df['latitude'].iloc[i]  # Latitude of the i-th row
    lon = df['longitude'].iloc[i]  # Longitude of the i-th row
   
    # Check if the point is within the first box
    if lat_min <= lat <= lat_max and lon_min <= lon <= lon_max:
        if not gevonden:  # Append only the first time a point is found in the first box
            rechtestuk_rijen.append(i)
            gevonden = True  # Set 'gevonden' flag to True

    # Check if the point is within the second box after finding a point in the first box
    if gevonden and lat_min2 <= lat <= lat_max2 and lon_min2 <= lon <= lon_max2:
        rechtestuk_rijen.append(i)
        gevonden = False  # Reset 'gevonden' flag to False after processing the second box
        
    #Optionally, you can print out each step to debug
    # print(f"i: {i}, lat: {lat}, lon: {lon}, gevonden: {gevonden}, rechtestuk_rijen: {rechtestuk_rijen}")

# Convert the list to a numpy array if needed

# Print the results
print("Indices of points in the two boxes:", rechtestuk_rijen)


Indices of points in the two boxes: [23269, 23617, 25366, 25692, 27374, 27706, 29377, 29708, 31545, 31897, 33690, 34034, 35891, 36243, 38094, 38440, 40345, 40704, 42621, 42995]


In [222]:
# Convert rechtestuk_rijen to integers to ensure compatibility with iloc indexing
rechtestuk_rijen = [int(idx) for idx in rechtestuk_rijen]

# Print the 'hoogte' value at the first index in rechtestuk_rijen
for i in range(len(rechtestuk_rijen)):
    print(df['hoogte'].iloc[rechtestuk_rijen[i]])


99.2
97.9
99.2
97.9
99.2
97.9
99.2
97.9
99.2
97.9
99.3
97.9
99.3
97.9
99.3
97.9
99.2
97.9
99.2
97.9


In [206]:
def haversine(lat1, lon1, lat2, lon2, radius=6371000):  # Radius in meters
    # Convert latitude and longitude from degrees to radians
    lat1, lon1, lat2, lon2 = map(math.radians, [lat1, lon1, lat2, lon2])
    
    # Compute differences
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    
    # Haversine formula
    a = math.sin(dlat / 2)**2 + math.cos(lat1) * math.cos(lat2) * math.sin(dlon / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    
    # Distance in meters
    distance = radius * c
    return distance

In [207]:
overstaande = ((df['hoogte'].iloc[rechtestuk_rijen[0]]) 
               - (df['hoogte'].iloc[rechtestuk_rijen[1]]))
print(overstaande)
lat1, lat2 = ((df['latitude'].iloc[rechtestuk_rijen[0]]), df['latitude'].iloc[rechtestuk_rijen[1]])
lon1, lon2 = ((df['longitude'].iloc[rechtestuk_rijen[0]]), df['longitude'].iloc[rechtestuk_rijen[1]])
aanliggende = haversine(lat1, lon1, lat2, lon2)
print(aanliggende)
alpha = math.atan(overstaande/aanliggende)
print(alpha)

1.2999999999999972
20389.035336202738
6.375975992989165e-05


In [208]:
yas = 'GPS latitude, in graden'
xas = 'GPS longitude, in graden'
colorbar = 'Wielsnelheid, in km/h'
data_file_motordriver = data_file_motordriver[data_file_motordriver[xas] != 0]
data_file_motordriver = data_file_motordriver[data_file_motordriver[yas] != 0]
data_file_motordriver = data_file_motordriver[data_file_motordriver[colorbar] != 0]
# Assuming 'data_file_motordriver' is your DataFrame and 'xas', 'yas' are the column names
# Filter rows from the dataset for the specific range
filter = data_file_master.iloc[ceil(len(data_file_master)*0.1):ceil(len(data_file_master)*0.3)]

# Create a figure for the scatter plot
plt.figure(figsize=(20, 20))

# Plot the data (replace merged_df with data_file_motordriver)
plt.scatter(data_file_motordriver[xas], data_file_motordriver[yas],c=data_file_motordriver[colorbar])

# Set the plot title and axis labels
plt.title('GPS data vs speed')
plt.ylabel('Latitude')
plt.xlabel('Longitude')

# Add a colorbar with a label for the speed in km/h (assuming you have speed data in 'speed' column)
cbar = plt.colorbar()
cbar.set_label('Speed (km/h)')


lat_min, lat_max = 0.00075 + 4.346357e3, 0.00060 + 4.346357e3
lon_min, lon_max = -2.552, -2.546
    
lat_min2, lat_max2 = 0.0005 + 4.346245e3, 0.0009 + 4.346245e3
lon_min2, lon_max2 = -2.392, -2.386
# Plot the rectangular boundary
plt.plot(
    [lon_min, lon_max, lon_max, lon_min, lon_min],
    [lat_min, lat_min, lat_max, lat_max, lat_min],
    color='red', linestyle='--', linewidth=2, label="Boundary Square")
    
plt.plot(
    [lon_min2, lon_max2, lon_max2, lon_min2, lon_min2],
    [lat_min2, lat_min2, lat_max2, lat_max2, lat_min2],
    color='red', linestyle='--', linewidth=2, label="Boundary Square")
    

In [255]:
massa = 200
g = 9.81
delta_h_list = []  # Initialize an empty list to store delta_h values
getallen_tussen_rechtestuk = []

# Iterate over every second index in the range
for i in range(0, len(rechtestuk_rijen) - 1, 2):  # Step of 2 ensures you skip every second pair
    lengtes_rechte_stuk = rechtestuk_rijen[i + 1] - rechtestuk_rijen[i]
    getallen_tussen_rechtestuk.append(lengtes_rechte_stuk)

print(getallen_tussen_rechtestuk)


# Calculate the change in height for each point in `rechtestuk_rijen`


# Dictionary to store datasets for each segment
delta_h_datasets = {}

# Initialize constants
massa = 90  # Mass in kg
g = 9.81     # Gravitational acceleration in m/s²

# Initialize an empty list to store the separate DataFrames for each segment
delta_h_datasets = {}

# Iterate through each segment defined in getallen_tussen_rechtestuk
for idx, section_length in enumerate(getallen_tussen_rechtestuk):
    start_index = rechtestuk_rijen[idx]  # Starting index of this segment
    
    # Lists to store delta_h and corresponding potential energy for the current segment
    delta_h_list = []
    potentiele_energie_list = []  # List to store potential energy values for the segment
    snelheid_list = []
    for offset in range(section_length):  # Loop through each point in the segment
        current_index = start_index + offset  # Index within the DataFrame
        
        if current_index >= len(df):  # Prevent out-of-bounds indexing
            break
        
        # Calculate delta_h relative to the first point of rechtestuk_rijen
        delta_h = df['hoogte'].iloc[current_index] - df['hoogte'].iloc[rechtestuk_rijen[1]]
        delta_h_list.append(delta_h)  # Append the computed delta_h
        
        # Calculate the corresponding potential energy
        potentiele_energie = massa * g * delta_h  # Potential energy in joules
        potentiele_energie_list.append(potentiele_energie)  # Append the potential energy
        # Voorbeeld: Snelheid berekenen uit potentiële energie

        # Snelheid berekenen
        snelheid = (2 * g * delta_h).apply(lambda x: np.sqrt(x) if x >= 0 else 0)
        snelheid_list.append(snelheid)
    # Store each segment as a separate DataFrame in the delta_h_datasets dictionary
    segment_name = f"Segment_{idx + 1}"
    delta_h_datasets[segment_name] = pd.DataFrame({
        'Index': range(start_index, start_index + len(delta_h_list)),
        'Delta_h': delta_h_list,
        'Potentiele Energie (J)': potentiele_energie_list,
        'Theoretische snelheid m/s' : snelheid_list
    })

# Display each separate dataset
for segment_name, dataset in delta_h_datasets.items():
    print(f"{segment_name}:")
    print(dataset)
    print()  # Print a newline for separation between datasets



[348, 326, 332, 331, 352, 344, 352, 346, 359, 374]


AttributeError: 'numpy.float64' object has no attribute 'apply'

In [252]:
rondje1 = delta_h_datasets["Segment_1"]
rondje2 = delta_h_datasets["Segment_2"]
rondje3 = delta_h_datasets["Segment_3"]
rondje4 = delta_h_datasets["Segment_4"]
rondje5 = delta_h_datasets["Segment_5"]
rondje6 = delta_h_datasets["Segment_6"]
rondje7 = delta_h_datasets["Segment_7"]
rondje8 = delta_h_datasets["Segment_8"]
rondje9 = delta_h_datasets["Segment_9"]
rondje10 = delta_h_datasets["Segment_10"]

rondje9

Index  Delta_h  Potentiele Energie (J)
0    31545      1.3                  2550.6
1    31546      1.3                  2550.6
2    31547      1.3                  2550.6
3    31548      1.3                  2550.6
4    31549      1.3                  2550.6
..     ...      ...                     ...
354  31899      0.0                     0.0
355  31900      0.0                     0.0
356  31901      0.0                     0.0
357  31902      0.0                     0.0
358  31903     -0.1                  -196.2

[359 rows x 3 columns]

In [253]:
df

timestamp    latitude  longitude  hoogte  speed_m/s  \
0      063448.30  4346.28356   -2.52589    99.5   0.038583   
1      063448.40  4346.28356   -2.52589    99.5   0.026237   
2      063448.50  4346.28356   -2.52589    99.4   0.035497   
3      063448.60  4346.28355   -2.52589    99.5   0.073051   
4      063448.70  4346.28356   -2.52589    99.4   0.064820   
...          ...         ...        ...     ...        ...   
46568       None  4346.27213   -2.51648    96.0        NaN   
46569       None  4346.27213   -2.51648    96.0        NaN   
46570       None  4346.27213   -2.51648    96.1        NaN   
46571       None  4346.27212   -2.51647    96.1        NaN   
46572       None  4346.27213   -2.51649    96.2        NaN   

       Theoretische Snelheid  
0                        0.0  
1                        0.0  
2                        0.0  
3                        0.0  
4                        0.0  
...                      ...  
46568                    0.0  
46569                    0.0  
46570                    0.0  
46571                    0.0  
46572                    0.0  

[46573 rows x 6 columns]